In [1]:
import hashlib # for grading

# Standard imports
import numpy as np
from numpy.testing import assert_allclose
import pandas as pd
import re
import string
import math
import warnings; warnings.simplefilter('ignore')

# NLTK imports
import nltk
nltk.download('stopwords')

from nltk.tokenize import WordPunctTokenizer
from nltk.stem.snowball import SnowballStemmer
from nltk.corpus import stopwords

# SKLearn related imports
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from sklearn.base import TransformerMixin

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/carmensc/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


# Q1. Cars Price

For the first question, you will be making use of regex to extract some information from the dataset `cars.txt` in the data folder. In this dataset, you'll find a list of cars that have been sold, as well as their brand, model and selling price.

Start by loading the data into a list of sentences. Each sentence is separated by a new line in the `.txt` file:


In [2]:
path = "data/cars.txt"
cars = []
with open(path, 'r', encoding='utf-8') as f:
    cars = [l.strip() for l in f.readlines()]

In [3]:
cars[:10]

['FORD -- Focus -- 19757',
 'LEXUS -- CT 200h -- 392',
 'JEEP -- Compass -- 22269',
 'CHEVROLET -- Captiva -- 7527',
 'SSANGYONG -- REXTON -- 34419',
 'TOYOTA -- Prius -- 251',
 'BMW -- 535 -- 23521',
 'BMW -- 328 -- 13485',
 'HYUNDAI -- Sonata -- 2901',
 'CHEVROLET -- Volt -- 3293']

In the first item, for example, `FORD` is the brand name, `Focus` is the model, and `19757` is the price.

#### Q1.a)

First, we want to see which `TOYOTA` cars have been sold. Return the full strings corresponding to cars that belong to this brand in a list assigned to a variable `ans`.

In [4]:
# ans = [ ... ]

# YOUR CODE HERE
toyota_pattern = re.compile(r"TOYOTA -- [A-Za-z0-9 ]+ -- \d+")
ans = [car for car in cars if toyota_pattern.match(car)]

In [5]:
assert len(ans) == 111
assert hashlib.sha256(' '.join(sorted(ans)).encode()).hexdigest() == \
    'e187e5b04c2a7cb863905c1abe8d5a791782dd80a1e3ae08430978e0bc5623e1'

### Q1.b)

Next, find all cars whose model is a set of numbers instead of characters. For example, `'BMW -- 535 -- 23521'`.

Return the full strings corresponding to these cars  in the variable `ans_models`.

In [6]:
# ans_models = ...

# YOUR CODE HERE
# Define a regex pattern to match car models that are sets of numbers instead of characters
model_number_pattern = re.compile(r"[A-Z]+ -- \d+ -- \d+$") #only accounting for uppercase

# Find all matches in the list of cars
ans_models = [car for car in cars if model_number_pattern.match(car)]

len(ans_models)

70

In [7]:
# Define a regex pattern to match car models that are exclusively numbers
model_number_pattern = re.compile(r"[A-Z-]+ -- \d+ -- \d+$")

# Find all matches in the list of cars with the exclusive pattern
ans_models = [car for car in cars if model_number_pattern.match(car)]

len(ans_models)

73

In [8]:
assert len(ans_models) == 73
assert hashlib.sha256(' '.join(sorted(ans_models)).encode()).hexdigest() == \
    '5f08454f40915f9cd36de32ed145322f618d01051db706c1f6f81c5e8877c8e7'

### Q1.c)

Finally, get the car brands and models whose selling price was bellow 1000.

Save the results in the list `ans_price`. Each element on this list should be in the format `BRAND -- MODEL`

In [9]:
# ans_price = ...

# YOUR CODE HERE

def extract_brand_model(cars_list):
    ans_price = []
    for car in cars_list:
        # Split the string by ' -- ' and strip to avoid leading/trailing whitespaces
        brand, model, price = map(str.strip, car.split(' -- '))
        # Check if the price is below 1000
        if int(price) < 1000:
            # Append to the list in the format "BRAND -- MODEL"
            ans_price.append(f'{brand} -- {model}')
    return ans_price

ans_price  = extract_brand_model(cars)

In [10]:
assert len(ans_price) == 77
assert hashlib.sha256(' '.join(sorted(ans_price)).encode()).hexdigest() == \
    '7b0ee55a70f3aab0435a140162df3f89aff25ba1b3b1c7b9c2b7d43e1660044d'

# Q2. Job postings (preprocessing)

The challenge of this exercise notebook is to classify job posting as 'Fake' or 'Real' using the posts' text. To do that, we first need to preprocess the data.

Let's start by briefly analyzing it:

In [11]:
df = pd.read_csv('data/job_postings.csv', index_col=0)

X = df['description']
y = df['fraudulent']

Let's look at an example of a job description and it's corresponding label:

In [12]:
df.iloc[10]['description']

"Inside Sales\n US, CA, Los Angeles\n 50000-55000\n GPL Technologies is a solutions provider focused on the design, implementation, and support of high-performance information technology systems.\xa0 Founded in Los Angeles, California in 2003, we draw on over a decade of expertise as trusted technology advisers, adding value for our customers by offering unique methods of improving IT efficiency, streamlining complex systems and environments, and reducing the costs associated with acquiring and maintaining IT systems.\xa0GPL cut its teeth serving the intense requirements of customers in the media and entertainment industry. \xa0We bring that work ethic with us to every customer: time is money, deadlines are non-negotiable, and the show must go on. \xa0Our company is comprised of creative, independent thinkers with a passion for technology. \xa0We love big data, fast networks, and solving the problems posed by today's digital media production pipelines.If serving clients who think a qua

In [13]:
df.iloc[10]['fraudulent']

0

Let's check the data size and distribution of classes:

In [14]:
def get_data_stats(X, y):
    print(f"Size of dataset: {len(X)}")
    unique, counts = np.unique(y, return_counts=True)
    print(f"Distribution of classes: {dict(zip(unique, counts))}")

get_data_stats(X, y)

Size of dataset: 1913
Distribution of classes: {0: 1047, 1: 866}


The classes are evenly distributed. We'll use a dev and test sets to be able to identify overfitting and check the performance on unseen data.

**Note**: So far you've used the `train`/`val`/`test` nomenclature for naming variables related to training, validation and test sets, respectively. `dev` is short for "development" and is just another typical identifier for the validation set, and we'll use it throughout this notebook instead of `val`

In [15]:
# train dev test split
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)
X_dev, X_test, y_dev, y_test = train_test_split(X_temp, y_temp, test_size=0.3, random_state=42, stratify=y_temp)
print(f"Train size: {len(X_train)}\nDev size: {len(X_dev)}\nTest size: {len(X_test)}")

Train size: 1530
Dev size: 268
Test size: 115


Since the goal is to turn the strings in X into useful features, now we will be performing common preprocessing operations on the texts.

#### Q2.a)

First, tokenize the data. Implement the function to receive a list of strings and an NLTK-style tokenizer, and return the list but with tokenized strings.

In [16]:
def apply_tokenizer(data, tokenizer):
    """
    Returns a list of sentences that have been tokenized with the provided `tokenizer`
    
    E.g. for an input ["This is a test!", "No, it can't be"],
         it should return ["This is a test !", "No , it can ' t be"]
    
    Args:
    data - list of strings containing the text to tokenize
    tokenizer - nltk tokenizer
    """
    
    # YOUR CODE HERE
    #data = data.fillna('')
    tokens = [' '.join(tokenizer.tokenize(text)) for text in data]
    return tokens

In [17]:
tokenizer = WordPunctTokenizer()
data_tok = apply_tokenizer(X_train, tokenizer)

assert len(data_tok) == 1530
assert isinstance (data_tok, list)
assert all(isinstance(sentence, str) for sentence in data_tok)

assert len([w for s in data_tok for w in s.split(" ")]) == 665508
assert hashlib.sha256(data_tok[100].encode()).hexdigest() == \
    '80a21ceb29cbdfda6f15e4c2def79894ca64f4231a8a9a27dbe9805d7c1a8c55'
assert hashlib.sha256(data_tok[875].encode()).hexdigest() == \
    '39c7f9fa57ecc57060c6db546fbdb4a2de201e41c6a6a466286c977039e94fdd'

#### Q2.b)

The second step you will implement is lowercasing the data.

In [18]:
def apply_lowercase(data):
    """
    Returns a list of strings, with all the tokens lowercased.
    
    Args:
    data - list of strings to be lowercased
    """

    # YOUR CODE HERE
    data_lower = [token.lower() for token in data]
    return data_lower

In [19]:
apply_lowercase(data_tok)

["account strategist ( non - profit experience needed ) us , ca , san diego nan stayclassy is a fast - growing san diego - based startup that develops an online fundraising product used by thousands of nonprofit organizations around the world . the company was founded in 2006 by a couple of friends who were looking to fundraise for charity , but didn ' t know how to get started . they envisioned a platform that made it easy for nonprofits to turn their supporters into fundraisers ; and so , they set off to build one . after years of testing their concept with dozens of nonprofits , their initial idea has evolved into what is now an industry - leading online fundraising solution for charities , foundations , churches , schools , clubs and more . recently , the founders were selected by bloomberg businessweek as one of the top 5 most promising social entrepreneurs in america . the company is also the host of the classy awards , the largest philanthropic awards show in the country . stayc

In [20]:
data_tok_lc = apply_lowercase(data_tok)

assert len(data_tok_lc) == 1530
assert isinstance (data_tok_lc, list)
assert all(isinstance(sentence, str) for sentence in data_tok_lc)
assert not any(c.isupper() for s in data_tok_lc for w in s.split(" ") for c in w)

assert len([w for s in data_tok_lc for w in s.split(" ")]) == 665508
assert hashlib.sha256(data_tok_lc[56].encode()).hexdigest() == \
    '1f5cf4311e169eb2f53d8b06f556362d06358a3259f302fa56bdf06dcd06136a'
assert hashlib.sha256(data_tok_lc[785].encode()).hexdigest() == \
    '4cb3727db93c102e455124d672acc00c629bb65f71a73a1a48f3ceb31619f9ff'

#### Q2.c)

Now implement a function that filters the stopwords. We will use NLTK's built-in English stopword list.

In [21]:
stopword_list = stopwords.words('english')

In [22]:
def apply_filter_stopwords(data, stopword_list):
    """
    Returns a list of strings, where the strings do not contain any of
        the stopwords in the given list.
    
    Args:
    data - list of strings to filter stopwords from
    stopword_list - list of stopwords to filter out
    """
    
    # Filter the stopwords from the text
    # data_no_stopwords = ...
    # YOUR CODE HERE
    data_no_stopwords = [' '.join(word for word in sentence.split(" ") if word not in stopword_list) 
                         for sentence in data]

    return data_no_stopwords


In [23]:
 apply_filter_stopwords(data_tok_lc, stopword_list)

["account strategist ( non - profit experience needed ) us , ca , san diego nan stayclassy fast - growing san diego - based startup develops online fundraising product used thousands nonprofit organizations around world . company founded 2006 couple friends looking fundraise charity , ' know get started . envisioned platform made easy nonprofits turn supporters fundraisers ; , set build one . years testing concept dozens nonprofits , initial idea evolved industry - leading online fundraising solution charities , foundations , churches , schools , clubs . recently , founders selected bloomberg businessweek one top 5 promising social entrepreneurs america . company also host classy awards , largest philanthropic awards show country . stayclassy fast - paced startup develops web - based fundraising & amp ; engagement software used thousands social impact organizations , including nonprofits social enterprises . company also host classy awards , largest social impact awards show country . 

In [24]:
data_tok_lc_nosw = apply_filter_stopwords(data_tok_lc, stopword_list)

assert len(data_tok_lc_nosw) == 1530
assert isinstance (data_tok_lc_nosw, list)
assert all(isinstance(sentence, str) for sentence in data_tok_lc_nosw)
assert not any(any(w in stopword_list for w in s.split(" ")) for s in data_tok_lc_nosw)

assert len([w for s in data_tok_lc_nosw for w in s.split(" ")]) == 472520
assert hashlib.sha256(data_tok_lc_nosw[325].encode()).hexdigest() == \
    '4b114a2e69b98612a8d5e6b47fc41411d3414f3a9f21740cc75eb9451787cf01'
assert hashlib.sha256(data_tok_lc_nosw[4].encode()).hexdigest() == \
    'ed242f390891d3f8dd5ef8b27f8f5e7031d8b3338c2790a7989c8bb0928fed9c'

#### Q2.d)

After filtering stopwords, we want to remove punctuation from the text as well. Consider only the tokens in `string.punctuation` to be single punctuation characters. Make sure to remove all punctuation and not only tokens that are single punctuation characters. 

_Hint: check the note on punctuation in Part 2 of the learning notebooks_

In [25]:
def apply_filter_punct(data):
    """
    Returns a list of tokenized sentences with no punctuation.
    
    Args:
    data - list of tokenized sentences from which to remove punctuation
    """

    # YOUR CODE HERE
    remove_punct_trans = str.maketrans('', '', string.punctuation)
    
    # Apply the translation table to each word in each sentence
    data_filt = [' '.join(word.translate(remove_punct_trans) for word in sentence.split()) for sentence in data]

    return data_filt


In [26]:
data_tok_lc_nosw_nopunct = apply_filter_punct(data_tok_lc_nosw)

#### Normalize whitespaces

Run the following function on `data_tok_lc_nosw_nopunct` before checking your answers, in case extra whitespaces cause the asserts to fail:

In [27]:
def normalize_whitespace(data):
    return [re.sub(r"^\s+|\s+$|(?<=\s)\s*", "", text) for text in data]

data_tok_lc_nosw_nopunct_norm = normalize_whitespace(data_tok_lc_nosw_nopunct)

In [28]:
len([w for s in data_tok_lc_nosw_nopunct_norm for w in s.split(" ")])

379730

In [29]:
assert len(data_tok_lc_nosw_nopunct_norm) == 1530
assert len([w for s in data_tok_lc_nosw_nopunct_norm for w in s.split(" ")]) == 379730
assert hashlib.sha256(data_tok_lc_nosw_nopunct_norm[74].encode()).hexdigest() == \
    '377fd8129ab959bb9b184093e6afe2a7812a579484bd63fdc28245736c37e442'
assert hashlib.sha256(data_tok_lc_nosw_nopunct_norm[965].encode()).hexdigest() == \
    '8ea25acf67aa0a5a36d5733f72cc7c3f345336c8044f390bee3b63ad31f8ac15'

#### Q2.e)

The last preprocessing step you are going to implement is stemming. Implement the function to receive an NLTK-style stemmer and return the text as a string with the stemmer applied.

In [30]:
def apply_stemmer(data, stemmer):
    """
    Returns a list of strings, with stemmed data.
    
    Args:
    data - list with text to stem
    stemmer - instance of stemmer to use
    """

    # YOUR CODE HERE
    stems = [' '.join(stemmer.stem(word) for word in sentence.split()) for sentence in data]
    return stems

In [31]:
stemmer = SnowballStemmer("english")
data_tok_lc_nosw_nopunct_norm_stem = apply_stemmer(data_tok_lc_nosw_nopunct_norm, stemmer)

In [32]:
stemmer = SnowballStemmer("english")
data_tok_lc_nosw_nopunct_norm_stem = apply_stemmer(data_tok_lc_nosw_nopunct_norm, stemmer)

assert len(data_tok_lc_nosw_nopunct_norm_stem) == 1530
assert len([w for s in data_tok_lc_nosw_nopunct_norm_stem for w in s.split(" ")]) == 379730
assert hashlib.sha256(data_tok_lc_nosw_nopunct_norm_stem[854].encode()).hexdigest() == \
    '59b37c27fe05b0e3d20df96df763b82dca7ec28fe2bd0164c10d257db852a63d'
assert hashlib.sha256(data_tok_lc_nosw_nopunct_norm_stem[21].encode()).hexdigest() == \
    'c116aa8dbd9c3f4785aae448aad52c2e9b2d9fd5b0f3b28e451affd8f3e3e8f1'

#### Q2.f)

Finally, join everything in a function, that applies the steps in the following order:
* Tokenization
* Lowercasing
* Filtering stopwords
* Filtering punctuation
* Normalizing whitespace
* Stemming

Make use of the functions you designed above when filling the transformer below.


In [33]:
# Custom transformer to implement sentence cleaning
class TextCleanerTransformer(TransformerMixin):
    def __init__(self, tokenizer, lower=True, remove_punct=True, stopwords=[], stemmer=None):
        self.tokenizer = tokenizer
        self.stemmer = stemmer
        self.lower = lower
        self.remove_punct = remove_punct
        self.stopwords = stopwords
    
    def clean_sentences(self, data):
                
        # Tokenize sentence so it each sentence contains spaced words or tokens
        # sentences_preprocessed = ...
        # YOUR CODE HERE
        sentences_preprocessed = apply_tokenizer(data, self.tokenizer)
        
        # Lowercase
        if self.lower:
            # sentences_preprocessed = ...
            # YOUR CODE HERE
            sentences_preprocessed = apply_lowercase(sentences_preprocessed)

        if self.stopwords:
            # sentences_preprocessed = ...
            # YOUR CODE HERE
            sentences_preprocessed = apply_filter_stopwords(sentences_preprocessed, self.stopwords)
            
        # Remove punctuation
        if self.remove_punct:
            # sentences_preprocessed = ...
            # YOUR CODE HERE
            sentences_preprocessed = apply_filter_punct(sentences_preprocessed)
        
        # Normalize whitespace
        # sentences_preprocessed = ...
        # YOUR CODE HERE
        sentences_preprocessed = normalize_whitespace(sentences_preprocessed)
    
        # Stem words
        if self.stemmer:
            # sentences_preprocessed = ...
            # YOUR CODE HERE
            sentences_preprocessed = apply_stemmer(sentences_preprocessed, self.stemmer)

        return sentences_preprocessed


In [34]:
text_cleaner = TextCleanerTransformer(
    WordPunctTokenizer(),
    lower=True, 
    remove_punct=True, 
    stopwords=stopwords.words('english'),
    stemmer=SnowballStemmer("english"),
)

X_train_pre = text_cleaner.clean_sentences(X_train)

In [35]:
assert len(X_train_pre) == 1530
assert len([w for s in X_train_pre for w in s.split(" ")]) == 379730
assert X_train_pre[1352][:150] == ('traffic manag web mobil mx mex mexico nan companyadcash ® intern advertis network deliv billion ad unit month reach sever million peopl around globe s')
assert X_train_pre[342][:150] == ('physic therapist us ca orovill nan welcom interfac rehabinterfac rehab provid comprehens rehabilit physic occup amp speech therapi amp consult servic ')

# Q3. Text classification

We will now use what we've learned to try to classify the job postings as fake or real. Let's first load the preprocessed data and double-check the balance of the classes.

We are loading the preprocessed csv file here. This way you won't be penalized if you were not able to finish the preprocessing part.

In [36]:
def load_dataset(file_name):
    """
    Loads a csv file and returns two lists, one
    containing only the text and one containing the labels
    
    Args:
    file_name: path to input file
    """
    df = pd.read_csv(file_name, index_col = 0)

    return list(df['description']), list(df['fraudulent'])

In [37]:
X_train_pre, y_train = load_dataset('data/job_postings_train_preprocessed.csv')
X_dev_pre, y_dev = load_dataset('data/job_postings_dev_preprocessed.csv')
X_test_pre, y_test = load_dataset('data/job_postings_test_preprocessed.csv')

In [38]:
get_data_stats(X_train_pre, y_train)

Size of dataset: 1530
Distribution of classes: {0: 837, 1: 693}


In [39]:
get_data_stats(X_dev_pre, y_dev)

Size of dataset: 268
Distribution of classes: {0: 147, 1: 121}


So, we should be aiming for much better than 45% accuracy, which is what we would get if we naively predicted `1` (fake) for everything.

#### Q3.a)

First, we'll look at the top X ngrams in each category to see if anything is interesting. Write a function that returns the most common n-grams and their count for a specific label in our dataset.


In [40]:
from nltk import ngrams
from collections import Counter

def top_ngrams_for_category(text, labels, filter_label, top_n=10, ngram_size=1):
    """
    Filters the data to the desired label, constructs a counter of ngrams
    Returns the top n ngrams
    
    Args:
    text: list of text strings to get ngrams from
    labels: categories corresponding to text
    filter_label: the label to filter the data on before getting ngrams
    top_n: top n ngrams to return
    ngram_size: the "n" in ngram (e.g. if ngram_size=2, return only bigrams)
    """
    # First, filter text to desired category
    # text_filtered = ...
    # YOUR CODE HERE
    text_filtered = [txt for txt, lbl in zip(text, labels) if lbl == filter_label]
    
    # Create list of ngrams
    # ngram_list = ...
    # YOUR CODE HERE
    ngram_list = []
    for t in text_filtered:
        # Split the text into words and generate ngrams
        words = t.split()
        ngram_list.extend(ngrams(words, ngram_size))
    
    # Count occurances of each ngram
    # hint: use collections.Counter
    # ngram_counter = ...
    # YOUR CODE HERE
    ngram_counter = Counter(ngram_list)
    
    # return top_n most common ngrams
    # hint: use a method of collections.Counter
    # return ...
    # YOUR CODE HERE
    return ngram_counter.most_common(top_n)

In [41]:
top_10_unigrams_real = top_ngrams_for_category(X_train_pre, y_train, 0, top_n=10, ngram_size=1)
assert top_10_unigrams_real == [(('nan',), 3199),
                                    (('work',), 2689),
                                    (('experi',), 1966),
                                    (('manag',), 1854),
                                    (('team',), 1830),
                                    (('servic',), 1773),
                                    (('develop',), 1706),
                                    (('custom',), 1624),
                                    (('compani',), 1430),
                                    (('time',), 1428)]
top_6_unigrams_fake = top_ngrams_for_category(X_train_pre, y_train, 1, top_n=6, ngram_size=1)
assert top_6_unigrams_fake == [(('nan',), 3318),
                                  (('work',), 1828),
                                  (('manag',), 1303),
                                  (('experi',), 1287),
                                  (('time',), 1221),
                                  (('servic',), 1187)]
top_5_bigrams_real = top_ngrams_for_category(X_train_pre, y_train, 0, top_n=5, ngram_size=2)
assert top_5_bigrams_real == [(('nan', 'nan'), 1349),
                                  (('full', 'time'), 745),
                                  (('custom', 'servic'), 398),
                                  (('bachelor', 'degre'), 308),
                                  (('year', 'experi'), 211)]
top_10_trigrams_fake = top_ngrams_for_category(X_train_pre, y_train, 1, top_n=10, ngram_size=3)
assert top_10_trigrams_fake == [(('nan', 'nan', 'nan'), 851),
                                 (('nan', 'full', 'time'), 165),
                                 (('time', 'nan', 'nan'), 138),
                                 (('high', 'school', 'equival'), 134),
                                 (('full', 'time', 'nan'), 131),
                                 (('oil', 'gas', 'industri'), 123),
                                 (('time', 'entri', 'level'), 116),
                                 (('full', 'time', 'entri'), 104),
                                 (('level', 'high', 'school'), 92),
                                 (('mid', 'senior', 'level'), 89)]

Looking at the top ngrams for each category, it doesn't seem like a BoW model will be very interesting, but let's try anyway.

#### Q3.b)
To begin, let's streamline our pipeline in a nice function. We'll use sklearn's `CountVectorizer` instead of the function we wrote. We'll also use the `LogisticRegression` classifier to make predictions on the dev set.

In [42]:
def train_and_validate(X_train, X_dev, y_train, y_dev, ngram_range=(1,1), max_features=None):
    """
    Train a model using sklearn's Pipeline and return it along with the predictions and the
    current accuracy in the validation set. Print the classification report as well.
    Assume the documents are already preprocessed
    
    Args:
    X_train - preprocessed articles in training data
    X_dev - preprocessed articles in dev data
    y_train - labels of training data
    y_dev - labels of dev data
    ngram_range - ngram range to use in CountVectorizer (tuple)
    max_features - max number of features to use in CountVectorizer (int)
    """
    
    # Build the pipeline containing the countvectorizer and the multinomial NB classifier
    # text_clf = Pipeline(...)
    
    # Train the classifier
    # (...)

    # y_dev_pred = (...)
    
    # acc = (...)
    
    # YOUR CODE HERE
    text_clf = Pipeline([('vect', CountVectorizer(ngram_range=ngram_range, max_features=max_features)),
                         ('clf', LogisticRegression())])
    
    # Train the classifier
    text_clf.fit(X_train, y_train)

    # Predict
    y_dev_pred = text_clf.predict(X_dev)
    
    # Accuracy
    acc = accuracy_score(y_dev, y_dev_pred)
    
    # print the classification report
    print(classification_report(y_dev, y_dev_pred))

    # return text_clf, y_dev_pred, acc
    # YOUR CODE HERE
    return text_clf, y_dev_pred, acc

In [43]:
clf, y_dev_pred, acc = train_and_validate(X_train_pre, X_dev_pre, y_train, y_dev)

# check same as before
assert_allclose(clf['clf'].intercept_, np.array([0.73381536]), rtol=1e-3)
assert ' '.join(str(i) for i in y_dev_pred[:20]) == "0 0 1 1 0 0 0 0 1 1 0 1 1 1 0 1 1 1 0 0"
assert hashlib.sha256(' '.join(str(i) for i in y_dev_pred).encode()).hexdigest() == \
    "7ed40ca221aaaf17d3647bd204045ae4799558b377e8ec37fbc464ee9731113a"
assert_allclose(acc, 0.90, rtol=1e-2)

              precision    recall  f1-score   support

           0       0.95      0.86      0.90       147
           1       0.85      0.94      0.89       121

    accuracy                           0.90       268
   macro avg       0.90      0.90      0.90       268
weighted avg       0.90      0.90      0.90       268



In [44]:
# we should also look at some misclassified examples
for text, pred, true in zip(X_dev_pre[:70], y_dev_pred[:70], y_dev[:70]):
    if pred != true:
        print(f"Sentence: {text}")
        print(f"Predicted: {pred}, Actual: {true}\n")

Sentence: android develop es vc valencia nan ehumanlif medic platform live onlin consult hd video call call doctor comfort home free sign doctor set fee consult connect symptom diagnosi topic interest best intern specialist mild ill may evalu immedi anywher avoid hassl urgent care doctor expand scope practic fix schedul enhanc intern reput care patient share knowledg medic webinar scientif articl mission tear barrier physician patient worldwid improv access healthcar enhanc communic within medic communiti lorem ipsum dolor sit amet liber populo appellantur et vis amet oporteat pri wisi indoctum explicari sadipsc nam liber interesset te quo te melius appareat delicatissimi eo lorem ipsum dolor sit amet liber populo appellantur et vis amet oporteat pri wisi indoctum explicari sadipsc nam liber interesset te quo te melius appareat delicatissimi eo vel sint semper atomorum habeo blandit sapientem nullam deseruiss vix ut te nominavi tincidunt temporibus per liber mucius oporter vel hinc qua

So just with the simplest BoW model we already get an accuracy of 0.9o! But let's see if we can do even better... In the misclassified examples, the last one even contains a strange url but classified as 'fake'. That's suspicious...

#### Q3.c)
Run the pipeline for different ngram ranges and/or with different values for max_features. Try to achieve an accuracy higher or equal to 0.9

In [45]:
# clf,y_dev_pred, acc = train_and_validate(...)
# YOUR CODE HERE
# Then, you should call this function in a loop with different parameters:
ngram_ranges = [(1, 1), (1, 2), (2, 2)]
max_features_opts = [None, 1000, 2000, 5000]

# Initialize best accuracy to zero
best_acc = 0
stop = False  # Flag to indicate when to break out of the outer loop

# Try different ngram ranges and max_features
for ngram_range in ngram_ranges:
    if stop:  # Check if we should stop iterating over ngram ranges
        break

    for max_features in max_features_opts:
        clf, y_dev_pred, acc = train_and_validate(X_train_pre, X_dev_pre, y_train, y_dev, 
                                                  ngram_range=ngram_range, 
                                                  max_features=max_features)
        print(f"ngram_range: {ngram_range}, max_features: {max_features}, Accuracy: {acc}")
        
        # Update best_acc if current model's accuracy is higher
        if acc > best_acc:
            best_acc = acc

        # If accuracy is 0.90 or higher, stop the loop
        if acc >= 0.90:
            stop = True  # Set the flag to True to break the outer loop
            break  # Break the inner loop

              precision    recall  f1-score   support

           0       0.95      0.86      0.90       147
           1       0.85      0.94      0.89       121

    accuracy                           0.90       268
   macro avg       0.90      0.90      0.90       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (1, 1), max_features: None, Accuracy: 0.8992537313432836
              precision    recall  f1-score   support

           0       0.94      0.82      0.88       147
           1       0.81      0.93      0.87       121

    accuracy                           0.87       268
   macro avg       0.88      0.88      0.87       268
weighted avg       0.88      0.87      0.87       268

ngram_range: (1, 1), max_features: 1000, Accuracy: 0.8731343283582089
              precision    recall  f1-score   support

           0       0.95      0.85      0.90       147
           1       0.84      0.95      0.89       121

    accuracy                           0.9

In [46]:
acc=0.0
count_ngrams = 1
while acc<0.90:
    clf,y_dev_pred, acc = train_and_validate(X_train_pre, X_dev_pre, y_train, y_dev, ngram_range=(1,count_ngrams))
    print(f"ngram_range: {ngram_range}, Accuracy: {acc}")
    count_ngrams += 1

              precision    recall  f1-score   support

           0       0.95      0.86      0.90       147
           1       0.85      0.94      0.89       121

    accuracy                           0.90       268
   macro avg       0.90      0.90      0.90       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (2, 2), Accuracy: 0.8992537313432836
              precision    recall  f1-score   support

           0       0.95      0.89      0.92       147
           1       0.88      0.94      0.91       121

    accuracy                           0.91       268
   macro avg       0.91      0.92      0.91       268
weighted avg       0.92      0.91      0.91       268

ngram_range: (2, 2), Accuracy: 0.914179104477612


In [47]:
assert(acc >= 0.90)

Now evaluate your model on the test set!

In [48]:
X_test_vec = clf['vect'].transform(X_test_pre)
y_test_pred = clf['clf'].predict(X_test_vec)
print(classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.95      0.94      0.94        63
           1       0.92      0.94      0.93        52

    accuracy                           0.94       115
   macro avg       0.94      0.94      0.94       115
weighted avg       0.94      0.94      0.94       115



Great! We were able to improve the model a little on the dev set and the performance on the test set is pretty good!

## Q4. TF-IDF

Similarly to how we found the top ngrams before we started working with BoW, we will now find the most important unigrams, inverse weighted by document frequency.

**Note**: Throughout this exercise, we'll use this term - **most important** - to refer to the unigrams of the highest weight, in particular within each class, since these will be transferred into vectors used for training. It is not 100% true these features will necessarily be "the most important", but in general they will be relevant, especially if your dataset is correctly processed, so we'll use this expression as a proxy.

#### Q4.a)

First, implement TF-IDF on a dataframe representing a Bag of Words model of the data. Here is a reminder of the TF-IDF formula:

$$ tfidf _{t, d} =(log{(1 + tf_{t,d})})*(log{(1 + \frac{N}{df_{t}})})  $$


In [49]:
# We'll start you off with the BoW representation, in pandas dataframe format
vec = CountVectorizer()
BoW_train = vec.fit_transform(X_train_pre)
BoW_train_df = pd.DataFrame(BoW_train.todense())

In [50]:
vec

CountVectorizer()

In [51]:
BoW_train

<1530x18647 sparse matrix of type '<class 'numpy.int64'>'
	with 239023 stored elements in Compressed Sparse Row format>

In [52]:
BoW_train_df

0      1      2      3      4      5      6      7      8      9      \
0         0      0      0      0      0      0      0      0      0      0   
1         0      0      0      0      0      0      0      0      0      0   
2         0      0      0      0      0      0      0      0      0      0   
3         0      0      0      0      0      0      0      0      0      0   
4         0      2      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
1525      0      2      0      0      0      0      0      0      0      0   
1526      2      0      0      0      0      0      0      0      0      0   
1527      0      0      0      0      0      0      0      0      0      0   
1528      0      0      0      0      0      0      0      0      0      0   
1529      0      0      0      0      0      0      0      0      0      0   

      ...  18637  18638  18639  18640  18641  18642  18643  18644  18645  \
0     ...      0      0      0      0      0      0      0      0      0   
1     ...      0      0      0      0      0      0      0      0      0   
2     ...      0      0      0      0      0      0      0      0      0   
3     ...      0      0      0      0      0      0      0      0      0   
4     ...      0      0      0      0      0      0      0      0      0   
...   ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
1525  ...      0      0      0      0      0      0      0      0      0   
1526  ...      0      0      0      0      0      0      0      0      0   
1527  ...      0      0      0      0      0      0      0      0      0   
1528  ...      0      0      0      0      0      0      0      0      0   
1529  ...      0      0      0      0      0      0      0      0      0   

      18646  
0         0  
1         0  
2         0  
3         0  
4         0  
...     ...  
1525      0  
1526      0  
1527      0  
1528      0  
1529      0  

[1530 rows x 18647 columns]

In [53]:
def tfidf(BoW_df):
    """
    Returns pandas dataframe of a tfidf representation from a BoW representation dataframe.

    Args:
    BoW_df - dataframe with document word counts (Bag of Words)
    """
    # remember that the BoW representation is raw counts, it is not normalized by the length of each text
    # first transform the df into term frequencies, where the counts are normalized
    # also double check the formula above for additional transformations applied to the tf expression
    # use np.log(x) for natural base log
    # tf = (...)
    # YOUR CODE HERE
    tf = BoW_df.div(BoW_df.sum(axis=1), axis=0)

    # now we need a function that computes the idf side of the expression
    # it operates over a column (a word in the vocab), where the column contains each doc's count of that word
    # def _idf(column):
    #   return (...)
    # YOUR CODE HERE
    def _idf(column):
        return np.log(1 + len(column) / sum(column > 0))

    # now weight the term frequencies by the idfs
    # tf_idf = (...)
    # YOUR CODE HERE
    tf_idf = (np.log(1 + tf)).multiply(BoW_df.apply(_idf))

    return tf_idf

In [54]:
tfidf_df = tfidf(BoW_train_df)
assert math.isclose(tfidf_df.iloc[1525, 1], 0.0175562, abs_tol=0.0001)
assert math.isclose(tfidf_df.iloc[0, 2505], 0.003557, abs_tol=0.0001)
assert math.isclose(tfidf_df.iloc[344, 3405], 0.0194850, abs_tol=0.0001)

In [55]:
tfidf_df

0         1      2      3      4      5      6      7      8      \
0     0.000000  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1     0.000000  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2     0.000000  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3     0.000000  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4     0.000000  0.029759    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...        ...       ...    ...    ...    ...    ...    ...    ...    ...   
1525  0.000000  0.017556    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1526  0.046614  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1527  0.000000  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1528  0.000000  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1529  0.000000  0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

      9      ...  18637  18638  18639  18640  18641  18642  18643  18644  \
0       0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1       0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2       0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3       0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4       0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...     ...  ...    ...    ...    ...    ...    ...    ...    ...    ...   
1525    0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1526    0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1527    0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1528    0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1529    0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

      18645  18646  
0       0.0    0.0  
1       0.0    0.0  
2       0.0    0.0  
3       0.0    0.0  
4       0.0    0.0  
...     ...    ...  
1525    0.0    0.0  
1526    0.0    0.0  
1527    0.0    0.0  
1528    0.0    0.0  
1529    0.0    0.0  

[1530 rows x 18647 columns]

### Q4.b)

Now that we have our TF-IDF representation, we can proceed with getting the most important words per category. 

Let's write a small helper function first to get the vocabulary in the right format.

In [56]:
# get the vocab from CountVectorizer, which is of the format {"word": idx, ...}
vocab_word_2_idx = vec.vocabulary_

In [57]:
# write a function to convert this vocab to the format {idx: "word", ...}

def reverse_vocab(vocab_word_to_index):
    """
    Converts a vocabulary dictionary with words as keys and indices as values to a 
        new dictionary with indices as keys and words as values
    
    Args:
    vocab_word_to_index: vocabulary dict of the format {"word": 0, "hello": 1, ...}
    """
    # YOUR CODE HERE
    return {v: k for k, v in vocab_word_to_index.items()}

In [58]:
vocab_idx_2_word = reverse_vocab(vocab_word_2_idx)
assert len(vocab_idx_2_word) == 18647
assert vocab_idx_2_word[1231] == "amount"
assert vocab_idx_2_word[1639] == "assimil"
assert vocab_idx_2_word[9876] == "memor"

In [59]:
vocab_idx_2_word

{783: 'account',
 15390: 'strategist',
 10639: 'non',
 12568: 'profit',
 6122: 'experi',
 10461: 'need',
 17332: 'us',
 2593: 'ca',
 14021: 'san',
 4788: 'diego',
 10382: 'nan',
 15307: 'stayclassi',
 6376: 'fast',
 7281: 'grow',
 1976: 'base',
 15272: 'startup',
 4671: 'develop',
 10935: 'onlin',
 6894: 'fundrais',
 12487: 'product',
 17344: 'use',
 16278: 'thousand',
 10644: 'nonprofit',
 11093: 'organ',
 1547: 'around',
 18073: 'world',
 3477: 'compani',
 6750: 'found',
 211: '2006',
 3881: 'coupl',
 6834: 'friend',
 9281: 'look',
 3015: 'chariti',
 8815: 'know',
 7067: 'get',
 15266: 'start',
 5797: 'envis',
 11894: 'platform',
 9377: 'made',
 5224: 'easi',
 16707: 'turn',
 15618: 'support',
 14399: 'set',
 2505: 'build',
 10928: 'one',
 18166: 'year',
 16160: 'test',
 3608: 'concept',
 5080: 'dozen',
 8172: 'initi',
 7857: 'idea',
 6007: 'evolv',
 8076: 'industri',
 8985: 'lead',
 14924: 'solut',
 6751: 'foundat',
 3117: 'church',
 14130: 'school',
 3301: 'club',
 13068: 'recent',

### Q4.c)

Finally, write a function to return the list of N most important words in each category according to TF-IDF.

In [60]:
def top_tfidf_words_for_category(tfidf_df, labels, filter_label, top_n=10):
    """
    Returns the top n most important words for the given label, with the given vocabulary
    and corresponding tfidf representation of some text data
    
    Args:
    tfidf_df: a dataframe of the tfidf representation of some text (columns=words, rows=documents)
    labels: categories corresponding to documents in tfidf_df
    filter_label: the label to filter the data on before getting top n words
    top_n: top n words to return
    """
    # First, filter tfidf to desired category
    # tfidf_filt = ...
    # YOUR CODE HERE
    labels = np.array(labels)
    tfidf_filt = tfidf_df[labels == filter_label]
    
    
    # Get the top n words of the current label, according to tfidf
    # There are several ways to do this, but here are some hints
    # 1) Sum the filtered df to get the total value per word
    # 2) Sort
    # 3) Replace indices with words and return the top_n
    
    ## Sum the TF-IDF scores for each word, which should return a Series
    word_scores = tfidf_filt.sum(axis=0)

    # Get the top n words based on their TF-IDF scores
    top_indices = word_scores.sort_values(ascending=False).head(top_n).index
    
    # Map indices to words using the feature names from the vectorizer
    # Assuming you have a vectorizer named 'vectorizer', change this as per your actual vectorizer variable name
    top_words = [vocab_idx_2_word[i] for i in top_indices]
    
    return top_words


# Get the top words for each category
top_15_fake = top_tfidf_words_for_category(tfidf_df, y_train, 1, top_n=15)
top_20_real = top_tfidf_words_for_category(tfidf_df, y_train, 0, top_n=20)

# Debugging: print the actual top words
print("Top 15 fake words:", top_15_fake)
print("Top 20 real words:", top_20_real)

# Make sure you've created vocab_idx_2_word beforehand using reverse_vocab function
#vocab_idx_2_word = reverse_vocab(vocab_word_2_idx)

Top 15 fake words: ['nan', 'work', 'time', 'entri', 'servic', 'custom', 'home', 'posit', 'experi', 'skill', 'amp', 'manag', 'administr', 'requir', 'start']
Top 20 real words: ['nan', 'work', 'develop', 'experi', 'manag', 'sale', 'custom', 'team', 'servic', 'product', 'job', 'market', 'client', 'design', 'busi', 'compani', 'time', 'technolog', 'nbsp', 'web']


In [61]:
top_15_fake

['nan',
 'work',
 'time',
 'entri',
 'servic',
 'custom',
 'home',
 'posit',
 'experi',
 'skill',
 'amp',
 'manag',
 'administr',
 'requir',
 'start']

In [62]:
top_15_fake = top_tfidf_words_for_category(tfidf_df, y_train, 1, top_n=15)
assert top_15_fake == ['nan',
                         'work',
                         'time',
                         'entri',
                         'servic',
                         'custom',
                         'home',
                         'posit',
                         'experi',
                         'skill',
                         'amp',
                         'manag',
                         'administr',
                         'requir',
                         'start']
top_20_real = top_tfidf_words_for_category(tfidf_df, y_train, 0, top_n=20)
assert top_20_real == ['nan',
                       'work',
                       'develop',
                       'experi',
                       'manag',
                       'sale',
                       'custom',
                       'team',
                       'servic',
                       'product',
                       'job',
                       'market',
                       'client',
                       'design',
                       'busi',
                       'compani',
                       'time',
                       'technolog',
                       'nbsp',
                       'web']

### Q4.d)

Now, we will put everything together. Rewrite the train_and_validate function from Q3.b but using sklearn's `TfIdfTransformer`. Also, add kwargs for CountVectorizer's `max_df` and `min_df`.

In [63]:
def train_and_validate_with_tfidf(X_train, X_dev, y_train, y_dev, ngram_range=(1,1),
                                  max_features=None, max_df=1.0, min_df=1):
    """
    Train a model using sklearn's Pipeline and return it along with the predictions and the
    current accuracy in the validation set. Print the classification report as well.
    Assume the documents are already preprocessed
    
    Args:
    X_train - preprocessed articles in training data
    X_dev - preprocessed articles in dev data
    y_train - labels of training data
    y_dev - labels of dev data
    ngram_range - ngram range to use in CountVectorizer (tuple)
    max_features - max number of features to use in CountVectorizer (int)
    max_df = max_df for CountVectorizer (int or float)
    min_df = min_df for CountVectorizer (int or float)
    """
    
    # Build a pipeline containing the countvectorizer, tfidftransformer and the logistic classifier
    # text_clf = Pipeline(...)
    text_clf = Pipeline([('vect', CountVectorizer(ngram_range=ngram_range, max_features=max_features, max_df=max_df, min_df=min_df)),
                   ('tfidf', TfidfTransformer()),
                   ('clf', LogisticRegression())])    
    # Train the classifier
    text_clf.fit(X_train, y_train)

    # y_dev_pred = 
    y_dev_pred = text_clf.predict(X_dev)
    
    # print the classification report
    acc = np.mean(y_dev_pred == y_dev)
    

    
    print(classification_report(y_dev, y_dev_pred))

    return text_clf, y_dev_pred, acc


In [64]:
clf, y_dev_pred, acc = train_and_validate_with_tfidf(X_train_pre, X_dev_pre, y_train, y_dev)

assert hashlib.sha256(" ".join([str(x) for x in list(y_dev_pred)]).encode()).hexdigest() == \
    "a63704cd531a94f5299f67f20b1e781e41f2f890825dee89fee6a4b536c05024"
assert_allclose(acc, 0.91, rtol=1e-3)

              precision    recall  f1-score   support

           0       0.90      0.94      0.92       147
           1       0.92      0.88      0.90       121

    accuracy                           0.91       268
   macro avg       0.91      0.91      0.91       268
weighted avg       0.91      0.91      0.91       268



In [65]:
# As before, we should also look at some misclassified examples
for text, pred, true in zip(X_dev_pre[:70], y_dev_pred[:70], y_dev[:70]):
    if pred != true:
        print(f"Sentence: {text}")
        print(f"Predicted: {pred}, Actual: {true}\n")

Sentence: data entri repres us tx austin 35000 40000 global connect world forc busi rethink communic mobil lifestyl flood technolog econom pressur alway ” mental creat opportun challeng organ size mitel ® nasdaq mitl tsx mnw global leader busi communic easili connect employe partner custom anywher anytim devic smallest busi largest enterpris mitel offer custom maximum choic one industri broadest portfolio best path cloud us 1 billion combin annual revenu 60 million custom worldwid 1 market share western europ mitel clear market leader busi communic respons review detail ticket ensur contain data requir custom monitor bin movement ensur activ seen match paperwork providedwatch contract level vs volum remain bin report discrep qualiti managerprovid ticket copi custom neededansw question custom may specif ticketsadvis plant manag miss paperworkcollect paperwork north south plant review bin inform includ sand pull correct bin bin movement line activ espons review detail ticket ensur contai

Unfortunately, we're still not able to correctly classify those sentences. Let's keep going and see if we can do even better.

#### Q4.e)

Use the `train_and_validate_with_tfidf` function you created before to train with different hyperparameters and get an accuracy score above 92% on the validation dataset. (This threshold is the same as what we got for plain CountVectorizer)


In [66]:
# clf, _, acc = train_and_validate_with_tfidf(...)
# YOUR CODE HERE
ngram_ranges = [(1, 1), (1, 2), (2, 2), (1, 3)]
max_features_opts = [None, 500, 1000, 2000, 5000, 10000]
max_df_opts = [0.5, 0.75, 1.0]
min_df_opts = [1, 2, 3, 5]

# Initialize best accuracy to zero
best_acc = 0
best_params = {}

# Try different combinations of ngram ranges, max_features, max_df, and min_df
for ngram_range in ngram_ranges:
    for max_features in max_features_opts:
        for max_df in max_df_opts:
            for min_df in min_df_opts:
                clf, y_dev_pred, acc = train_and_validate_with_tfidf(
                    X_train_pre, X_dev_pre, y_train, y_dev,
                    ngram_range=ngram_range,
                    max_features=max_features,
                    max_df=max_df,
                    min_df=min_df
                )
                print(f"ngram_range: {ngram_range}, max_features: {max_features}, "
                      f"max_df: {max_df}, min_df: {min_df}, Accuracy: {acc}")
                
                # Update best_acc and best_params if current model's accuracy is higher
                if acc > best_acc:
                    best_acc = acc
                    best_params = {
                        'ngram_range': ngram_range,
                        'max_features': max_features,
                        'max_df': max_df,
                        'min_df': min_df
                    }
                    
                # If the accuracy is greater or equal to 0.92, break out of all loops
                if best_acc >= 0.92:
                    break
            if best_acc >= 0.92:
                break
        if best_acc >= 0.92:
            break
    if best_acc >= 0.92:
        break

print(f"Best accuracy: {best_acc} with parameters: {best_params}")

              precision    recall  f1-score   support

           0       0.89      0.95      0.91       147
           1       0.93      0.85      0.89       121

    accuracy                           0.90       268
   macro avg       0.91      0.90      0.90       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (1, 1), max_features: None, max_df: 0.5, min_df: 1, Accuracy: 0.9029850746268657
              precision    recall  f1-score   support

           0       0.89      0.95      0.91       147
           1       0.93      0.85      0.89       121

    accuracy                           0.90       268
   macro avg       0.91      0.90      0.90       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (1, 1), max_features: None, max_df: 0.5, min_df: 2, Accuracy: 0.9029850746268657
              precision    recall  f1-score   support

           0       0.89      0.95      0.91       147
           1       0.93      0.85      0.89      

              precision    recall  f1-score   support

           0       0.86      0.88      0.87       147
           1       0.85      0.83      0.84       121

    accuracy                           0.86       268
   macro avg       0.86      0.86      0.86       268
weighted avg       0.86      0.86      0.86       268

ngram_range: (1, 1), max_features: 500, max_df: 1.0, min_df: 2, Accuracy: 0.8582089552238806
              precision    recall  f1-score   support

           0       0.87      0.88      0.88       147
           1       0.86      0.83      0.85       121

    accuracy                           0.86       268
   macro avg       0.86      0.86      0.86       268
weighted avg       0.86      0.86      0.86       268

ngram_range: (1, 1), max_features: 500, max_df: 1.0, min_df: 3, Accuracy: 0.8619402985074627
              precision    recall  f1-score   support

           0       0.86      0.88      0.87       147
           1       0.85      0.83      0.84       1

              precision    recall  f1-score   support

           0       0.88      0.93      0.91       147
           1       0.91      0.85      0.88       121

    accuracy                           0.90       268
   macro avg       0.90      0.89      0.89       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (1, 1), max_features: 2000, max_df: 0.75, min_df: 2, Accuracy: 0.8955223880597015
              precision    recall  f1-score   support

           0       0.88      0.93      0.91       147
           1       0.91      0.85      0.88       121

    accuracy                           0.90       268
   macro avg       0.90      0.89      0.89       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (1, 1), max_features: 2000, max_df: 0.75, min_df: 3, Accuracy: 0.8955223880597015
              precision    recall  f1-score   support

           0       0.88      0.93      0.91       147
           1       0.91      0.85      0.88    

              precision    recall  f1-score   support

           0       0.89      0.95      0.91       147
           1       0.93      0.85      0.89       121

    accuracy                           0.90       268
   macro avg       0.91      0.90      0.90       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (1, 1), max_features: 10000, max_df: 0.5, min_df: 2, Accuracy: 0.9029850746268657
              precision    recall  f1-score   support

           0       0.89      0.95      0.91       147
           1       0.93      0.85      0.89       121

    accuracy                           0.90       268
   macro avg       0.91      0.90      0.90       268
weighted avg       0.90      0.90      0.90       268

ngram_range: (1, 1), max_features: 10000, max_df: 0.5, min_df: 3, Accuracy: 0.9029850746268657
              precision    recall  f1-score   support

           0       0.88      0.93      0.91       147
           1       0.91      0.85      0.88    

In [67]:
acc=0.0
count_ngrams = 1
while acc<0.92:
    clf, _, acc = train_and_validate_with_tfidf(X_train, X_dev, y_train, y_dev, ngram_range=(1,count_ngrams),max_features=None, max_df=1.0, min_df=1)
    print(f"ngram_range: {ngram_range}, Accuracy: {acc}")
    count_ngrams += 1

              precision    recall  f1-score   support

           0       0.89      0.92      0.90       147
           1       0.90      0.86      0.88       121

    accuracy                           0.89       268
   macro avg       0.89      0.89      0.89       268
weighted avg       0.89      0.89      0.89       268

ngram_range: (1, 2), Accuracy: 0.8917910447761194
              precision    recall  f1-score   support

           0       0.89      0.95      0.92       147
           1       0.94      0.86      0.90       121

    accuracy                           0.91       268
   macro avg       0.91      0.91      0.91       268
weighted avg       0.91      0.91      0.91       268

ngram_range: (1, 2), Accuracy: 0.9104477611940298
              precision    recall  f1-score   support

           0       0.90      0.96      0.93       147
           1       0.95      0.88      0.91       121

    accuracy                           0.92       268
   macro avg       0.93     

In [68]:
assert(acc > 0.92)

Now evaluate your model on the test set!

In [69]:
X_test_vec = clf['tfidf'].transform(clf['vect'].transform(X_test_pre))
y_test_pred = clf['clf'].predict(X_test_vec)
print(classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.96      0.75      0.84        63
           1       0.76      0.96      0.85        52

    accuracy                           0.84       115
   macro avg       0.86      0.85      0.84       115
weighted avg       0.87      0.84      0.84       115



Great results! We were able to slightly improve the performance on the test set compared with using BoW with n-grams ranging from 1 to 3.